# VHH Design in Engine Python Client

### Getting started 

[Install the Engine Python Client](https://levitate.bio/api/api-python-library/)

In a terminal, type:
- conda activate engine 
  - Recommended Python version: 3.7 <= version <= 3.10
- juptyer notebook

In [ ]:
# import the engine client after installation and authorization
from engine import EngineClient
import os
import pandas as pd
import glob

client = EngineClient()

## Helper Functions

In [ ]:
from Bio.PDB import PDBParser, PPBuilder
from Bio.SeqRecord import SeqRecord
from Bio.Seq import Seq
from Bio import SeqIO
import os

def pdb_to_fasta_per_chain(pdb_file):
    """
    Extracts amino acid sequences from each chain in a multi-chain PDB file
    and writes each sequence to a separate FASTA file. Returns a list of the
    fasta file paths. 

    Args:
        pdb_file (str): Path to the input PDB file.
        output_dir (str): Directory to save output FASTA files.
    """
    parser = PDBParser(QUIET=True)
    structure = parser.get_structure("structure", pdb_file)
    ppb = PPBuilder()
    basename = pdb_file.split(".pdb")[0]

    # if not os.path.exists(output_dir):
    #     os.makedirs(output_dir)

    chains_found = set()

    all_chains = []

    for model in structure:
        for chain in model:
            chain_id = chain.id
            if chain_id in chains_found:
                continue  # avoid duplicates in multi-model structures
            chains_found.add(chain_id)

            peptides = ppb.build_peptides(chain)
            if not peptides:
                print(f"No peptide sequence found in chain {chain_id}.")
                continue

            sequence = ''.join(str(peptide.get_sequence()) for peptide in peptides)
            fasta_file = os.path.join(f"{basename}_chain_{chain_id}.fasta")
            record = SeqRecord(Seq(sequence), id=f"Chain_{chain_id}", description="")
            SeqIO.write(record, fasta_file, "fasta")
            print(f"Chain {chain_id} sequence written to {fasta_file}")

            all_chains.append(fasta_file)

    return all_chains

import tarfile

def unpack_tgz(tgz_filepath, extract_path='.'):
    """
    Unpacks a .tgz file.

    Args:
        tgz_filepath (str): Path to the .tgz file.
        extract_path (str, optional): Path to extract the contents to. 
                                     Defaults to the current directory.
    """
    try:
        with tarfile.open(tgz_filepath, 'r:gz') as tar:
            tar.extractall(path=extract_path)
        print(f"Successfully extracted '{tgz_filepath}' to '{extract_path}'")
    except FileNotFoundError:
        print(f"Error: File not found: '{tgz_filepath}'")
    except tarfile.ReadError:
        print(f"Error: Could not open '{tgz_filepath}'. It may not be a valid .tgz file.")
    except Exception as e:
         print(f"An unexpected error occurred: {e}")

<br>

## Step 1: Predict my complex structure

### Colabsearch MSA generation

In [ ]:
help(client) #documentation for each submission command that you can access here in the notebook

In [ ]:
#generate multisequence alignments for your inputs
vhh_colabsearch = client.submit_colab_search(fasta_path = "vhh.fasta")
antigen_colabsearch = client.submit_colab_search(fasta_path = "antigen.fasta")

In [ ]:
# Check the status of the jobs
print(client.get_status(vhh_colabsearch)) # print the status of the job

In [ ]:
# Check the status of the jobs
print(client.get_status(antigen_colabsearch)) # print the status of the job

In [ ]:
# Get the results of the job
vhh_colabsearch_output = client.get_results(vhh_colabsearch) # get the results as a dictionary
print(vhh_colabsearch_output.items()) #see what the output key is called to dump the results

In [ ]:
vhh_colabsearch_output['msa'].dump('vhh-colabsearch-results') #dump the models from a the dictionary value

In [ ]:
antigen_colabsearch_output = client.get_results(antigen_colabsearch) # same process for the antigen msa
antigen_colabsearch_output['msa'].dump('antigen-colabsearch-results')

### Boltz structure prediction 

In [ ]:
# Submit the job

boltzJob = client.submit_boltz1(fasta_paths=["vhh.fasta", "antigen.fasta"], 
                                msa_paths=["vhh.msa","antigen.msa"]
) # submit target and vhh chains 

# Check the status of the job
print(client.get_status(boltzJob)) # print the status of the job

In [ ]:
# Check the status of the job
print(client.get_status(boltzJob)) # print the status of the job

In [ ]:
# Get the results of the job
boltzOutput = client.get_results(boltzJob) # get the results as a dictionary
print(boltzOutput.items()) #see what the output key is called to dump the results

In [ ]:
boltzOutput['predictions'].dump('boltz-results') #dump the models from a the dictionary value
!ls 'boltz-results/output/boltz_results_output/predictions/output/' #show the contents of the output directory

In [ ]:
!cat 'boltz-results/output/boltz_results_output/predictions/output/confidence_output_model_0.json' #show the confidence

<br>

## Step 2: Relax the output 

In [ ]:
# Submit the job to perform Rosetta structure optimization on the complex
relaxJob = client.submit_relax(pdb_path = "boltz-results/output/boltz_results_output/predictions/output/output_model_0.pdb", repeats = 10)

# Check the status of the job
print(client.get_status(relaxJob))

In [ ]:
# Check the status of the job
print(client.get_status(relaxJob))

In [ ]:
# Get the results of the job
relaxOutput = client.get_results(relaxJob) # get the results as a dictionary
print(relaxOutput.items()) #see what the output key is called to dump the results

In [ ]:
relaxOutput['models'].dump('relax-results') #dump the models from a the dictionary value
relaxOutput['scores'].dump('relax-results') #dump the scores from a the dictionary value

!ls 'relax-results' #show the contents of the output directory

In [ ]:
# Filter using Pandas
pd.set_option('display.max_colwidth', 100) # Set maximum column width to 100 characters

# Show data as a dataframe
scores = pd.read_csv('relax-results/scores.sc',sep='\s+').sort_values(by="total_score") 
display(scores)

# Pick the best scoring repeat
best_relax = scores.iloc[0]["description"]
print(best_relax)

In [ ]:
unpack_tgz('relax-results/models.tgz', 'relax-results/models')

!ls 'relax-results' #show the contents of the output directory

In [ ]:
print(f"relax-results/models/{best_relax}.pdb") #this printed path is used in the next step

<br>

## Step 3: Identify thermostabilizing mutations

In [ ]:
#run thermompnn for in silico scanning mutagenesis
thermompnnJob = client.submit_thermo_mpnn(
    pdb_path="relax-results/models/input.pdb", #the best scoring relax PDB from step 2
    chain="B" #the vhh chain
)

In [ ]:
# Check the status of the job
print(client.get_status(thermompnnJob)) # print the status of the job

In [ ]:
# Get the results of the job
thermompnnOutput = client.get_results(thermompnnJob) # get the results as a dictionary
print(thermompnnOutput.items()) #see what the output key is called to dump the results

In [ ]:
thermompnnOutput['ddgs'].dump('thermompnn-results') #dump the models from a the dictionary value
thermompnnOutput['heatmap'].dump('thermompnn-results') #dump the models from a the dictionary value
!ls 'thermompnn-results' #show the contents of the output directory

In [ ]:
import numpy as np
import csv
import seaborn as sns
import matplotlib.pyplot as plt

# Load the CSV file
df = pd.read_csv('thermompnn-results/ThermoMPNN_inference_input.csv')  # Replace with your actual filename

# Filter for ddG values less than -0.5
df_filtered = df[df['ddG_pred'] < -1.0]

# Pivot the data into a matrix format suitable for a heatmap
heatmap_data = df_filtered.pivot(index='mutation', columns='position', values='ddG_pred')

# Optional: sort amino acids and positions (if desired)
heatmap_data = heatmap_data.sort_index(axis=0)  # sort positions
heatmap_data = heatmap_data[sorted(heatmap_data.columns)]  # sort amino acids

# Create the heatmap
plt.figure(figsize=(12, 8))
sns.heatmap(heatmap_data, cmap='coolwarm', center=0, annot=True)
plt.title('Site Saturation Mutagenesis ddG Heatmap')
plt.xlabel('Amino Acid')
plt.ylabel('Position')
plt.tight_layout()


In [ ]:
display(df_filtered[["position","wildtype","mutation","ddG_pred"]]) #shows the potential thermostabilizing mutations

<br>

## Step 4: Redesign the VHH

### Example with Rosetta Design

In [ ]:
designJob = client.submit_design(
    pdb_path="relax-results/models/input.pdb",
    resfile_path="vhh.res",
    repeats=100
)

In [ ]:
# Check the status of the job
print(client.get_status(designJob))

In [ ]:
designOutput = client.get_results(designJob) # get the results as a dictionary
print(designOutput.items()) #see what the output key is called to dump the results

# Get the results of the job
designOutput['models'].dump('design-results') #dump the models from a the dictionary value

In [ ]:
# Filter using Pandas
pd.set_option('display.max_colwidth', 100) # Set maximum column width to 100 characters

# Show data as a dataframe
scores = pd.read_csv('design-results/results/scores.sc',sep='\s+')
display(scores)

scores.describe()

<br>

## Step 5: Interface analysis on designs

In [ ]:
design_pdbs = glob.glob("design-results/results/*pdb")

In [ ]:
analyzerJob = client.submit_interface_analyzer(
    pdb_paths=design_pdbs,
    mode="analyzer",
    interface1="A",
    interface2="B",
    batch_size=10
)

In [ ]:
# Check the status of the job
print(client.get_status(analyzerJob))

In [ ]:
# Get the results of the job
analyzerOutput = client.get_results(analyzerJob) # get the results as a dictionary
print(analyzerOutput.items()) #see what the output key is called to dump the results

In [ ]:
analyzerOutput['scores'].dump('analyzer-results') #dump the scores from a the dictionary value

!ls 'analyzer-results' #show the contents of the output directory

In [ ]:
# Filter using Pandas
pd.set_option('display.max_colwidth', 100) # Set maximum column width to 100 characters

# Show data as a dataframe
scores = pd.read_csv('analyzer-results/score.sc',sep='\s+').sort_values(by="dG_separated") 
display(scores.head())

# Pick the best design by 
best_binder = scores.iloc[0]["description"]
print(best_binder)

<br>

## Step 6: Solubility scoring on the designs

In [ ]:
solubilityJob = client.submit_solubility_score(
    pdb_paths=design_pdbs,
    batch_size=10
)

In [ ]:
# Check the status of the job
print(client.get_status(solubilityJob))

In [ ]:
# Get the results of the job
solubilityOutput = client.get_results(solubilityJob) # get the results as a dictionary
print(solubilityOutput.items()) #see what the output key is called to dump the results

In [ ]:
solubilityOutput['scores'].dump('solubility-results') #dump the scores from a the dictionary value

!ls 'solubility-results' #show the contents of the output directory

In [ ]:
# Show data as a dataframe
scores = pd.read_csv('solubility-results/predictions.csv',sep='\s+')
structures = scores.loc[scores['residue_number'] == "TOTAL"] #shows the total scores for each model
display(structures.head())

In [ ]:
residues = scores.loc[scores['residue_number'] != "TOTAL"] #shows the per-residue scores
residues.head()